In [1]:
import os
import sys
import multiprocessing
import warnings

import pandas as pd
import numpy as np

from Bio import SeqIO
from glob import glob
from functools import partial
sys.path.append('../../')
from hamp_pred.external.lbs.sequence import mmseqs2

In [5]:
data_dir = '../../data/input'

# Get HAMP sequences

In [6]:
# read and cluster sequences from https://pubmed.ncbi.nlm.nih.gov/20184894/
msa = list(SeqIO.parse(os.path.join(data_dir, 'hamp_msa.fasta'), 'fasta'))

msa_df = pd.DataFrame(
        [(str(i.seq).replace('-', ''), i.id) for i in msa],
    columns=['sequence', 'id']
)

In [7]:
# remove redundancy at 70% ident and 70% coverage
cl = mmseqs2.MMSeqsClusterer()
msa_df_clustered = cl.cluster(msa_df, min_identity=0.7, coverage=0.7)

createdb /tmp/w212w22i tmp/17849725013188194778/input --max-seq-len 65535 --dont-split-seq-by-len 1 --dbtype 0 --dont-shuffle 1 --id-offset 0 --compressed 0 -v 3 

Converting sequences
[
Time for merging files: 0h 0m 0s 25ms
Time for merging files: 0h 0m 0s 23ms
Time for merging files: 0h 0m 0s 1ms
Time for processing: 0h 0m 0s 173ms
kmermatcher tmp/17849725013188194778/input tmp/17849725013188194778/clu_tmp/5951097914207075492/linclust/16764076073124638189/pref --sub-mat blosum62.out --alph-size 13 --min-seq-id 0.7 --kmer-per-seq 21 --adjust-kmer-len 0 --mask 0 --mask-lower-case 0 --cov-mode 0 -k 0 -c 0.7 --max-seq-len 65535 --hash-shift 5 --split-memory-limit 0 --include-only-extendable 0 --skip-n-repeat-kmer 0 --threads 20 --compressed 0 -v 3 

Database size: 6456 type: Aminoacid
Reduced amino acid alphabet: (A S T) (C) (D B N) (E Q Z) (F Y) (G) (H) (I V) (K R) (L J M) (P) (W) (X) 

Estimated memory consumption 2 MB
Generate k-mers list for 1 split
[=================================

[=================================================================] 5.56K 0s 3ms
Index statistics
Entries:          83252
DB size:          488 MB
Avg k-mer size:   0.001301
Top 10 k-mers
    DEGLTF	82
    EIQAFN	62
    DEGLNF	49
    EIDAFN	35
    RREGAR	32
    EIQSFN	21
    PVSDGQ	20
    IGMREV	19
    DEGMTV	16
    PVSDGR	14
Time for index table init: 0h 0m 0s 480ms
k-mer similarity threshold: 154
	k-mers per position = 0.475694, k-mer match probability: 0.000000
k-mer match probability: 0.000000

Starting prefiltering scores calculation (step 1 of 1)
Query db start  1 to 5561
Target db start  1 to 5561
[=================================================================] 5.56K 0s 8ms

0.473296 k-mers per position
27 DB matches per sequence
0 overflows
6 sequences passed prefiltering per query sequence
3 median result list length
0 sequences with 0 size result lists

Time for prefiltering scores calculation: 0h 0m 0s 11ms
Time for merging files: 0h 0m 0s 20ms
Time for processing: 0h 0m 

In [8]:
msa_df_clustered = msa_df_clustered.groupby('clust_id').head(1)
len(msa_df_clustered)

5388

In [9]:
msa_df_clustered.to_pickle(os.path.join(data_dir, 'hamp_master.p'))

# Get AF2 models

In [10]:
def extract_models(models_dir, out_path, df_clustered):
    for out_file in glob(os.path.join(models_dir, '*', '*result.zip')):

        seq_id = int(out_file.split('/')[-1].replace('.result.zip', '').split("_")[1])
        assert seq_id in df_clustered.index

        tmp = os.path.join(out_path, str(seq_id))
        os.system(f'mkdir {tmp}')

        os.system(f'unzip -j "{out_file}" "*relaxed*.pdb" -d {tmp}')

In [11]:
#
# af2 model files are avaliable upon request 
#
models_dir = '/home/nfs/jludwiczak/calc/hamp_olek/hamp_final/out'
out_path = os.path.join(data_dir, 'af2_full')
df_clustered = pd.read_pickle(os.path.join(data_dir, 'hamp_master.p'))

# get aligned sequences
msa = list(SeqIO.parse(os.path.join(data_dir, 'hamp_msa.fasta'), 'fasta'))
hampid2alnseq = pd.DataFrame(
        [(str(i.seq), i.id) for i in msa],
    columns=['sequence', 'id']
)

In [13]:
# unzip af2 models bundles
extract_models(models_dir, out_path, df_clustered)

Archive:  /home/nfs/jludwiczak/calc/hamp_olek/hamp_final/out/hamp_48/hamp_5586.result.zip
 extracting: ../../data/input/af2_full/5586/hamp_5586_unrelaxed_rank_1_model_5.pdb  
 extracting: ../../data/input/af2_full/5586/hamp_5586_relaxed_rank_1_model_5.pdb  
 extracting: ../../data/input/af2_full/5586/hamp_5586_unrelaxed_rank_2_model_2.pdb  
 extracting: ../../data/input/af2_full/5586/hamp_5586_relaxed_rank_2_model_2.pdb  
 extracting: ../../data/input/af2_full/5586/hamp_5586_unrelaxed_rank_3_model_1.pdb  
 extracting: ../../data/input/af2_full/5586/hamp_5586_relaxed_rank_3_model_1.pdb  
 extracting: ../../data/input/af2_full/5586/hamp_5586_unrelaxed_rank_4_model_3.pdb  
 extracting: ../../data/input/af2_full/5586/hamp_5586_relaxed_rank_4_model_3.pdb  
 extracting: ../../data/input/af2_full/5586/hamp_5586_unrelaxed_rank_5_model_4.pdb  
 extracting: ../../data/input/af2_full/5586/hamp_5586_relaxed_rank_5_model_4.pdb  
Archive:  /home/nfs/jludwiczak/calc/hamp_olek/hamp_final/out/hamp_62/h

 extracting: ../../data/input/af2_full/6215/hamp_6215_unrelaxed_rank_1_model_1.pdb  
 extracting: ../../data/input/af2_full/6215/hamp_6215_relaxed_rank_1_model_1.pdb  
 extracting: ../../data/input/af2_full/6215/hamp_6215_unrelaxed_rank_2_model_2.pdb  
 extracting: ../../data/input/af2_full/6215/hamp_6215_relaxed_rank_2_model_2.pdb  
 extracting: ../../data/input/af2_full/6215/hamp_6215_unrelaxed_rank_3_model_3.pdb  
 extracting: ../../data/input/af2_full/6215/hamp_6215_relaxed_rank_3_model_3.pdb  
 extracting: ../../data/input/af2_full/6215/hamp_6215_unrelaxed_rank_4_model_5.pdb  
 extracting: ../../data/input/af2_full/6215/hamp_6215_relaxed_rank_4_model_5.pdb  
 extracting: ../../data/input/af2_full/6215/hamp_6215_unrelaxed_rank_5_model_4.pdb  
 extracting: ../../data/input/af2_full/6215/hamp_6215_relaxed_rank_5_model_4.pdb  
Archive:  /home/nfs/jludwiczak/calc/hamp_olek/hamp_final/out/hamp_56/hamp_2983.result.zip
 extracting: ../../data/input/af2_full/2983/hamp_2983_unrelaxed_rank_1

 extracting: ../../data/input/af2_full/623/hamp_623_relaxed_rank_1_model_4.pdb  
 extracting: ../../data/input/af2_full/623/hamp_623_unrelaxed_rank_2_model_1.pdb  
 extracting: ../../data/input/af2_full/623/hamp_623_relaxed_rank_2_model_1.pdb  
 extracting: ../../data/input/af2_full/623/hamp_623_unrelaxed_rank_3_model_3.pdb  
 extracting: ../../data/input/af2_full/623/hamp_623_relaxed_rank_3_model_3.pdb  
 extracting: ../../data/input/af2_full/623/hamp_623_unrelaxed_rank_4_model_2.pdb  
 extracting: ../../data/input/af2_full/623/hamp_623_relaxed_rank_4_model_2.pdb  
 extracting: ../../data/input/af2_full/623/hamp_623_unrelaxed_rank_5_model_5.pdb  
 extracting: ../../data/input/af2_full/623/hamp_623_relaxed_rank_5_model_5.pdb  
Archive:  /home/nfs/jludwiczak/calc/hamp_olek/hamp_final/out/hamp_56/hamp_2981.result.zip
 extracting: ../../data/input/af2_full/2981/hamp_2981_unrelaxed_rank_1_model_3.pdb  
 extracting: ../../data/input/af2_full/2981/hamp_2981_relaxed_rank_1_model_3.pdb  
 extr

 extracting: ../../data/input/af2_full/622/hamp_622_unrelaxed_rank_2_model_2.pdb  
 extracting: ../../data/input/af2_full/622/hamp_622_relaxed_rank_2_model_2.pdb  
 extracting: ../../data/input/af2_full/622/hamp_622_unrelaxed_rank_3_model_3.pdb  
 extracting: ../../data/input/af2_full/622/hamp_622_relaxed_rank_3_model_3.pdb  
 extracting: ../../data/input/af2_full/622/hamp_622_unrelaxed_rank_4_model_1.pdb  
 extracting: ../../data/input/af2_full/622/hamp_622_relaxed_rank_4_model_1.pdb  
 extracting: ../../data/input/af2_full/622/hamp_622_unrelaxed_rank_5_model_5.pdb  
 extracting: ../../data/input/af2_full/622/hamp_622_relaxed_rank_5_model_5.pdb  
Archive:  /home/nfs/jludwiczak/calc/hamp_olek/hamp_final/out/hamp_56/hamp_810.result.zip
 extracting: ../../data/input/af2_full/810/hamp_810_unrelaxed_rank_1_model_4.pdb  
 extracting: ../../data/input/af2_full/810/hamp_810_relaxed_rank_1_model_4.pdb  
 extracting: ../../data/input/af2_full/810/hamp_810_unrelaxed_rank_2_model_2.pdb  
 extract

 extracting: ../../data/input/af2_full/3096/hamp_3096_unrelaxed_rank_1_model_3.pdb  
 extracting: ../../data/input/af2_full/3096/hamp_3096_relaxed_rank_1_model_3.pdb  
 extracting: ../../data/input/af2_full/3096/hamp_3096_unrelaxed_rank_2_model_1.pdb  
 extracting: ../../data/input/af2_full/3096/hamp_3096_relaxed_rank_2_model_1.pdb  
 extracting: ../../data/input/af2_full/3096/hamp_3096_unrelaxed_rank_3_model_4.pdb  
 extracting: ../../data/input/af2_full/3096/hamp_3096_relaxed_rank_3_model_4.pdb  
 extracting: ../../data/input/af2_full/3096/hamp_3096_unrelaxed_rank_4_model_2.pdb  
 extracting: ../../data/input/af2_full/3096/hamp_3096_relaxed_rank_4_model_2.pdb  
 extracting: ../../data/input/af2_full/3096/hamp_3096_unrelaxed_rank_5_model_5.pdb  
 extracting: ../../data/input/af2_full/3096/hamp_3096_relaxed_rank_5_model_5.pdb  
Archive:  /home/nfs/jludwiczak/calc/hamp_olek/hamp_final/out/hamp_56/hamp_3325.result.zip
 extracting: ../../data/input/af2_full/3325/hamp_3325_unrelaxed_rank_1

...

 extracting: ../../data/input/af2_full/1981/hamp_1981_unrelaxed_rank_1_model_4.pdb  
 extracting: ../../data/input/af2_full/1981/hamp_1981_relaxed_rank_1_model_4.pdb  
 extracting: ../../data/input/af2_full/1981/hamp_1981_unrelaxed_rank_2_model_2.pdb  
 extracting: ../../data/input/af2_full/1981/hamp_1981_relaxed_rank_2_model_2.pdb  
 extracting: ../../data/input/af2_full/1981/hamp_1981_unrelaxed_rank_3_model_1.pdb  
 extracting: ../../data/input/af2_full/1981/hamp_1981_relaxed_rank_3_model_1.pdb  
 extracting: ../../data/input/af2_full/1981/hamp_1981_unrelaxed_rank_4_model_5.pdb  
 extracting: ../../data/input/af2_full/1981/hamp_1981_relaxed_rank_4_model_5.pdb  
 extracting: ../../data/input/af2_full/1981/hamp_1981_unrelaxed_rank_5_model_3.pdb  
 extracting: ../../data/input/af2_full/1981/hamp_1981_relaxed_rank_5_model_3.pdb  
Archive:  /home/nfs/jludwiczak/calc/hamp_olek/hamp_final/out/hamp_51/hamp_385.result.zip
 extracting: ../../data/input/af2_full/385/hamp_385_unrelaxed_rank_1_mo

 extracting: ../../data/input/af2_full/1827/hamp_1827_unrelaxed_rank_1_model_1.pdb  
 extracting: ../../data/input/af2_full/1827/hamp_1827_relaxed_rank_1_model_1.pdb  
 extracting: ../../data/input/af2_full/1827/hamp_1827_unrelaxed_rank_2_model_4.pdb  
 extracting: ../../data/input/af2_full/1827/hamp_1827_relaxed_rank_2_model_4.pdb  
 extracting: ../../data/input/af2_full/1827/hamp_1827_unrelaxed_rank_3_model_3.pdb  
 extracting: ../../data/input/af2_full/1827/hamp_1827_relaxed_rank_3_model_3.pdb  
 extracting: ../../data/input/af2_full/1827/hamp_1827_unrelaxed_rank_4_model_2.pdb  
 extracting: ../../data/input/af2_full/1827/hamp_1827_relaxed_rank_4_model_2.pdb  
 extracting: ../../data/input/af2_full/1827/hamp_1827_unrelaxed_rank_5_model_5.pdb  
 extracting: ../../data/input/af2_full/1827/hamp_1827_relaxed_rank_5_model_5.pdb  
Archive:  /home/nfs/jludwiczak/calc/hamp_olek/hamp_final/out/hamp_51/hamp_2502.result.zip
 extracting: ../../data/input/af2_full/2502/hamp_2502_unrelaxed_rank_1

 extracting: ../../data/input/af2_full/1999/hamp_1999_unrelaxed_rank_1_model_2.pdb  
 extracting: ../../data/input/af2_full/1999/hamp_1999_relaxed_rank_1_model_2.pdb  
 extracting: ../../data/input/af2_full/1999/hamp_1999_unrelaxed_rank_2_model_4.pdb  
 extracting: ../../data/input/af2_full/1999/hamp_1999_relaxed_rank_2_model_4.pdb  
 extracting: ../../data/input/af2_full/1999/hamp_1999_unrelaxed_rank_3_model_5.pdb  
 extracting: ../../data/input/af2_full/1999/hamp_1999_relaxed_rank_3_model_5.pdb  
 extracting: ../../data/input/af2_full/1999/hamp_1999_unrelaxed_rank_4_model_1.pdb  
 extracting: ../../data/input/af2_full/1999/hamp_1999_relaxed_rank_4_model_1.pdb  
 extracting: ../../data/input/af2_full/1999/hamp_1999_unrelaxed_rank_5_model_3.pdb  
 extracting: ../../data/input/af2_full/1999/hamp_1999_relaxed_rank_5_model_3.pdb  
Archive:  /home/nfs/jludwiczak/calc/hamp_olek/hamp_final/out/hamp_51/hamp_2001.result.zip
 extracting: ../../data/input/af2_full/2001/hamp_2001_unrelaxed_rank_1

 extracting: ../../data/input/af2_full/1241/hamp_1241_relaxed_rank_1_model_2.pdb  
 extracting: ../../data/input/af2_full/1241/hamp_1241_unrelaxed_rank_2_model_3.pdb  
 extracting: ../../data/input/af2_full/1241/hamp_1241_relaxed_rank_2_model_3.pdb  
 extracting: ../../data/input/af2_full/1241/hamp_1241_unrelaxed_rank_3_model_4.pdb  
 extracting: ../../data/input/af2_full/1241/hamp_1241_relaxed_rank_3_model_4.pdb  
 extracting: ../../data/input/af2_full/1241/hamp_1241_unrelaxed_rank_4_model_1.pdb  
 extracting: ../../data/input/af2_full/1241/hamp_1241_relaxed_rank_4_model_1.pdb  
 extracting: ../../data/input/af2_full/1241/hamp_1241_unrelaxed_rank_5_model_5.pdb  
 extracting: ../../data/input/af2_full/1241/hamp_1241_relaxed_rank_5_model_5.pdb  
Archive:  /home/nfs/jludwiczak/calc/hamp_olek/hamp_final/out/hamp_51/hamp_1989.result.zip
 extracting: ../../data/input/af2_full/1989/hamp_1989_unrelaxed_rank_1_model_2.pdb  
 extracting: ../../data/input/af2_full/1989/hamp_1989_relaxed_rank_1_m

 extracting: ../../data/input/af2_full/1986/hamp_1986_unrelaxed_rank_2_model_1.pdb  
 extracting: ../../data/input/af2_full/1986/hamp_1986_relaxed_rank_2_model_1.pdb  
 extracting: ../../data/input/af2_full/1986/hamp_1986_unrelaxed_rank_3_model_2.pdb  
 extracting: ../../data/input/af2_full/1986/hamp_1986_relaxed_rank_3_model_2.pdb  
 extracting: ../../data/input/af2_full/1986/hamp_1986_unrelaxed_rank_4_model_3.pdb  
 extracting: ../../data/input/af2_full/1986/hamp_1986_relaxed_rank_4_model_3.pdb  
 extracting: ../../data/input/af2_full/1986/hamp_1986_unrelaxed_rank_5_model_5.pdb  
 extracting: ../../data/input/af2_full/1986/hamp_1986_relaxed_rank_5_model_5.pdb  
Archive:  /home/nfs/jludwiczak/calc/hamp_olek/hamp_final/out/hamp_51/hamp_6364.result.zip
 extracting: ../../data/input/af2_full/6364/hamp_6364_unrelaxed_rank_1_model_2.pdb  
 extracting: ../../data/input/af2_full/6364/hamp_6364_relaxed_rank_1_model_2.pdb  
 extracting: ../../data/input/af2_full/6364/hamp_6364_unrelaxed_rank_2

# Measure AF2 models with SamCC

In [18]:
# To measure af2 hamp models use samCC turbo https://academic.oup.com/bioinformatics/article/36/22-23/5368/6039120
sys.path.append('../../hamp_pred/')
from utils.measure import measure_one_HAMP, get_ref_crick
from utils.tools import diffangle

In [19]:
def run_multiprocess(func, tasks, n_cores, tasks_per_core=1):  
    stdout_queue = multiprocessing.Queue()
    pool = multiprocessing.Pool(processes=n_cores, initargs=[stdout_queue], maxtasksperchild=tasks_per_core)
    for i, data in enumerate(pool.map(func, tasks), 1):
        yield data
    pool.close()
    pool.join()

In [20]:
# referece Crick angles
crangles = {'a':19.5,'b':122.35,'c':-134.78,'d': -31.92,'e':70.92 ,'f':173.78,'g':-83.35}

# aa names mapping
AA_3_to_1 = {'CYS': 'C', 'ASP': 'D', 'SER': 'S', 'GLN': 'Q', 'LYS': 'K',
             'ILE': 'I', 'PRO': 'P', 'THR': 'T', 'PHE': 'F', 'ASN': 'N', 
             'GLY': 'G', 'HIS': 'H', 'LEU': 'L', 'ARG': 'R', 'TRP': 'W', 
             'ALA': 'A', 'VAL':'V', 'GLU': 'E', 'TYR': 'Y', 'MET': 'M'}

In [21]:
# define ranges for helix 1 and helix 2 in MSA
h1_msa_start = 5 #4
h1_msa_stop = 18

h2_msa_start = 85 # 84
h2_msa_stop = 98

start_hep = 'a' #g

In [22]:
warnings.filterwarnings(action='ignore', category=UserWarning)

In [23]:
data=[]

for idx in df_clustered.index:
    
    row = df_clustered.loc[idx]
    group = row['id'].split("|")[1]
    true_id = int(row['id'].split("|")[0])
        
    # aligned sequence
    alnseq = hampid2alnseq.loc[idx].sequence
    
    # cut helix1 and helix2
    h1 = alnseq[h1_msa_start:h1_msa_stop].replace('-', '')
    h2 = alnseq[h2_msa_start:h2_msa_stop].replace('-', '')
    
    if len(h1) != len(h2): 
        continue
        
    seq = row.sequence    
    if seq.find('X')>-1: 
        continue

    # measure model        
    h1_start = seq.find(h1); assert h1_start > -1
    h2_start = seq.find(h2); assert h2_start > -1
    
    a1_start, a1_stop = h1_start+1, h1_start+len(h1)+1
    a2_start, a2_stop = h2_start+1, h2_start+len(h2)+1
    chain1, chain2 = 'A', 'B'
    
    kwargs = {'a1_start':a1_start, 
              'a1_stop':a1_stop,
              'a2_start':a2_start,
              'a2_stop':a2_stop,
              'chain1':chain1,
              'chain2':chain2}
    
    print(h1, h2, idx, true_id, group)
    
    mapfunc = partial(measure_one_HAMP, **kwargs)
    
    # get 1 rank af2 model
    pdb_files = sorted(glob(os.path.join(out_path, str(idx), '*_relaxed*.pdb')), key=lambda x:int(x.split('/')[-1].split("_")[4]))
    pdb_files = [pdb_files[0]]
    
    for job, pdb_file in zip(run_multiprocess(mapfunc, pdb_files, len(pdb_files)), pdb_files):    
        
        bundle_df, n_crick_mut, c_crick_mut = job

        n_crick_mut = n_crick_mut[2:-2]
        c_crick_mut = c_crick_mut[2:-2]
        n_P = c_P = 3.5 

        c_phi = n_phi = crangles[start_hep] 

        n_crick_ref = get_ref_crick(n_P, n_phi)[:len(n_crick_mut)]
        c_crick_ref = get_ref_crick(c_P, c_phi)[:len(c_crick_mut)]

        n_crick_diff = diffangle(n_crick_mut, n_crick_ref)
        n_crick_diff = (n_crick_diff[0::2] + n_crick_diff[1::2])/2

        c_crick_diff = diffangle(c_crick_mut, c_crick_ref)
        c_crick_diff = (c_crick_diff[0::2] + c_crick_diff[1::2])/2

        n_crick_diff = np.mean(n_crick_diff)
        c_crick_diff = np.mean(c_crick_diff)

        # rotation asymmetry
        crick_diff = diffangle(n_crick_diff, c_crick_diff) 

        seq1 = bundle_df.res_name[0::4].tolist()
        seq2 = bundle_df.res_name[1::4].tolist()
        seq1 = "".join([AA_3_to_1[res] for res in seq1])
        seq2 = "".join([AA_3_to_1[res] for res in seq2])
        
        assert seq1 == h1 and seq2 == h2

        data.append(
                (true_id, group, n_crick_diff, c_crick_diff, crick_diff, h1, h2, n_crick_mut, c_crick_mut, seq)
            )
        
data_df = pd.DataFrame(data, columns=['idx', 'group', 'n_rot', 'c_rot', 'rot', 'n_seq', 'c_seq', 'n_crick_mut', 'c_crick_mut', 'full_seq'])
assert data_df['idx'].is_unique
data_df.set_index('idx', inplace=True)
len(data_df)

PLKELVQGVQRIA EIGELITSFNLMA 0 0 A_group_13
PIRELVEGVRSIA ELGELIASFNDMA 1 1 A_group_13
PIKELLDGVKNIA ELGELIVNFNEMA 2 2 A_group_13
PLSELRKGIRRVA ELGDLILQFNDMG 14 14 A_group_13
PVKELLRGVRAVA ELGELVNGFNDMA 15 15 A_group_13
PIKELLAGIRNIS QIGELIFSFNNMA 16 16 A_group_13
PQKKLLLGIQNIA QLSTLIISFNEMA 17 17 A_group_13
PLDILSNGVMQIS EFAPVCADFNEMA 18 18 A_group_14
PLELLSYGAEQIK EFGQVCGDFDEMR 19 19 A_group_14
PLELLSYGAGQIE EFAKVCRDFDKMR 20 20 A_group_14
PLQKLSRGTKEIK EFGEVCRDFDEMR 21 21 A_group_14
PLVKLKQAAEKMG EVGELCESFENMR 22 22 A_group_14
PVGKMREATKSIK ELGQLCGDLEDMR 23 23 A_group_14
PLQQLLEATQKIA EMGALCEAFDLMR 24 24 A_group_14
PIRKLSEAAGKIS ELGQLSNTFEDMR 25 25 A_group_14
PLDVLKRATKEMK EIGQLCEDFEEMR 26 26 A_group_14
PLSQLKQASEQIK EIGELFVAFEEMR 27 27 A_group_14
PLKELQYASNEIR EFGEAIKSFEGMR 28 28 A_group_14
PLVKLRKATQNIK EFSELCRDFEEMR 29 29 A_group_14
PLAKLQAAARNIK EIGQLCQDFEEMR 30 30 A_group_14
PLNKLQEATKKIR EIGQLCQDFEEMR 31 31 A_group_14
PLNQLKIGTEKIK EIGELCDAFDSMR 32 32 A_group_14
PITALKEGAQRIK EI

PILRLNDAAKKLS ELGELANSFNSMA 244 244 A_group_27
PILQLNSAAKEIS ELGELANSFDQMA 245 245 A_group_27
PLRRMNYIMSLQE EFADLANHFDALL 247 247 A_group_38
PLERMTRTMEEVE EIGTVAAHLDTLL 248 248 A_group_38
PLEQMARTMQQVE EIGRLAAHLDHLL 249 249 A_group_38
PLERIGATFEKVG EIAELALALDGVL 250 250 A_group_38
PMTRMVGTMRALK ELGQLARQFDQLL 251 251 A_group_38
PLEQMNRTIAAVD EIGLVARRFDELL 254 254 A_group_38
PIERMHATIGRID ELGRLATAFDHLL 255 255 A_group_38
PIERMHATMHAIE ELGVVAAHFDRLL 260 260 A_group_38
PIERMAAVMGRIE ELGGLARSFDRLL 261 261 A_group_38
PIERMHGTIGRIE ELGLLAREFDRLL 264 264 A_group_38
PIQHLINTSKEIA EIGQLAITFNEMA 265 265 A_group_44
PVRKLGRATRELA ELADLAKTFNETA 266 266 A_group_44
PLNDIISVSKEIT ELGQLAVHFNKMA 267 267 A_group_44
PVRALNTAASQLG ELAQLVTTFNHTA 268 268 A_group_44
SLQKLQAGTAEIA EVEDLAKSFNYMS 269 269 A_group_44
PVRELRRAADSMG EMADLARTFNSSA 270 270 A_group_44
PVQRLGDAARRLG ELADLSRTFNRTA 271 271 A_group_44
PVRALRRATRSIA ELADLSRTFNETA 273 273 A_group_44
PIKQIIEASMKIS EIGELAVNFNHMA 274 274 A_group_44
PVLHLKDVSDEIA

PLLLLAEGTKAVA ELGTLTQSFNMMT 466 479 A_group_6
PLLLLAEGVKQVA ELGGLTRSFADMT 467 480 A_group_6
PVNDLVAAARRVA EIGTLGSAFNRMT 472 485 A_group_63
PLLDLFYATRKVQ EMSTLARAFNQMT 473 486 A_group_63
PIGRLASAAHTVR ELHALGHSFNAMT 474 487 A_group_63
PLAELVSAARTIG EIGLLARAFNRMT 475 488 A_group_63
PLTDLVAAARKVG EIGLLNRAFNRMT 476 489 A_group_63
PISHMVEAVRRIG EIGTLGFAFNRMA 477 490 A_group_63
PIRTLISAADEVS DLANLGETFNKMT 479 492 A_group_63
PIRLLISAADDVA DIGQLSKTFNYMV 480 493 A_group_63
PIRRLIAATDQVS DLAHLGETFNKMT 481 494 A_group_63
PIRLLISAADSVA DVGRLSRTFNKMV 482 495 A_group_63
PVSGLVQAAGRVS EIRALSIAFNMMT 483 496 A_group_63
PIRRLINAADQVA DLQHLGESFNKMT 484 497 A_group_63
PLGLLILAAQRIS EVTGLSRAFNSMT 486 499 A_group_63
PISRLVAAAERVR EIAALARAFNRMT 491 504 A_group_63
PIGRLIDAAEKVR EIGVLSRAFNRMT 492 505 A_group_63
PVGRLAGAVQRVG EIAMLGRGFNQMT 493 506 A_group_63
PLGTLIGATRTAA EISVLTRAFNRMT 494 507 A_group_63
PIGRLAEASEQVG EIQTLGESFNRMT 500 513 A_group_63
PLGLLILASGRIS ELSSLSRAFNRMT 501 514 A_group_63
PIRRLMSAADHVA D

PMNLINQSMRNLE ELSDLAHEFNDMI 731 744 A_mgroup_108
PLNDIQETVEVLS ELGELAWMFNEMI 732 745 A_mgroup_108
PMRKIKQTINAVN ELSDLAVVFNDML 733 746 A_mgroup_108
PIKKMSQISHDIN ELGELAISFNEML 734 747 A_mgroup_108
PLNKLMAACASIE ELGLLAQTFSSMT 735 748 A_mgroup_109
PLNDLVDACKQVK ELGILAHTFSKMS 736 749 A_mgroup_109
PLHHLVAASHAMT ELGQLGNAFNHMT 737 750 A_mgroup_109
PLNQLMRASTQIE ELGRLAKSFTHMS 738 751 A_mgroup_109
PLGQLISASEQIQ ELGILGNAFRNMA 739 752 A_mgroup_109
PLNQLVTASRQVK ELGLLSSAFTQMA 740 753 A_mgroup_109
PLNQLVAASGKVQ EIGILADNFSKMS 741 754 A_mgroup_109
PLKQLTQASIQVQ ELGNLARAFSQMS 742 755 A_mgroup_109
PLNHLVIASLQME ELGLLSRTFNHMS 743 756 A_mgroup_109
PLNAMVDASEKIK EMGILCRTFNSMA 744 757 A_mgroup_109
PISELTLLSTKMS EIDELGENFNRMS 745 758 A_mgroup_110
PLVGLNEVAKEMS EIGQLGETLNFLT 746 759 A_mgroup_110
PIRELARLSDRMA EIGELGENFNRMS 747 760 A_mgroup_110
PIMELAGLSQEMA EIGVLGNNFNKMS 748 761 A_mgroup_110
PITQLASLSRRMS EIGTLGNNFNIMS 750 763 A_mgroup_110
PIRSLAALSARMS EIGVLGHSMNTLS 752 765 A_mgroup_110
PILVLENIAKKMS EIGQLG

PLEDLEAGAVAVA EVRRLTRTFNHMS 929 942 A_mgroup_55
PLSRLARAAQVLS EIRDLNASFNRMA 932 945 A_mgroup_55
SVKALQDGTRDIA EFGQLALDFSSMA 933 946 A_mgroup_57
SLNDLQSQFDHLS EFGQLANRFNQMA 934 947 A_mgroup_57
TTTDLQTQFNAVI ELGQLSHSFNKMT 935 948 A_mgroup_57
IIDDLQNQFESIY ELGALTQRFNYIS 936 949 A_mgroup_57
ASQDLQHQFDSIS ELGQMSAKFNRMA 937 950 A_mgroup_57
SVEALREKFTQLS EFGQLSKEFNYMA 938 951 A_mgroup_57
TVDDLQTQFDAIY ELGQLSARFNQMA 939 952 A_mgroup_57
FCTDLQAQCNAVI ELGLLAQSFNQMT 940 953 A_mgroup_57
TTKDLQAQFDAVR ELGQLSAGFNEMA 941 954 A_mgroup_57
PLRRVAQVLDAVA EIGRMAASLQRAT 942 955 A_mgroup_59
PLDRVRAVLEALA ELGQMAAALERAT 943 956 A_mgroup_59
PIDQTATALRALA EVGQMATALNVAS 944 957 A_mgroup_59
PLNRCVEVLERTA ELGRLAAALNTAT 945 958 A_mgroup_59
PLGRTVAALESVA EVGRLASALNTTV 946 959 A_mgroup_59
PVRLLLAGTREVE EIGELAAAFNRMI 948 961 A_mgroup_60
RITDLIGGLNRIE ELGRLSDSLNNMA 949 962 A_mgroup_60
RITAVVGGIHRFS EMASLAISFNQMA 950 963 A_mgroup_60
RITGMISGIHAFQ EMGELAASFNRMA 952 965 A_mgroup_60
RITHVVDGIHRFE ELAELARAFNRMA 953 966 A_mg

...

PLRQALGLAERIS ESGQLLRAMQQMQ 5799 5795 BACKGROUND
PIERVAAASETLA ELGVLQQSFNTMA 5800 5796 BACKGROUND
PIKRLTQVMQNAA EISQLAKAYNFMN 5801 5797 BACKGROUND
PVARVTEVVRDVA EVRLMAQSFNKML 5802 5798 BACKGROUND
PIRRLLAATRRIA EVAELGDAFNTMV 5803 5799 BACKGROUND
ETRALADVLGQLA EDLARVWARLDET 5804 5800 BACKGROUND
PLVELVKAVDRVA EVGRLADAFNRMT 5805 5801 BACKGROUND
PLSQMERVANHLA EIGRLGKAFNKMA 5806 5802 BACKGROUND
PVAELSEAASRVA EVGRLAAAFNHMT 5807 5803 BACKGROUND
PIQELKKFAEEIS EIGQLAESLEKMK 5808 5804 BACKGROUND
PILRLAHVSEAIS EIGLLQQNFNRMA 5809 5805 BACKGROUND
PLKQLSQNVQAVG EIGQLTKAFNQML 5810 5806 BACKGROUND
PLVALKGVANQIA EVGELAKSLKLMA 5811 5807 BACKGROUND
PINTLIEHTERIS EIGKLAEAFERMR 5812 5808 BACKGROUND
PLEKVVSAAEQIA EIGMLARAFMKMT 5813 5809 BACKGROUND
PLRQLAASARRIE EVGMLASSFNNMA 5814 5810 BACKGROUND
PVRELAQAAHRVA EVGQLAAAFNTMV 5815 5811 BACKGROUND
PLQGLTKAVQRVG EVGQLATAFNGMA 5816 5812 BACKGROUND
PLKRLTEAANILS EIGKLANAFNKMS 5817 5813 BACKGROUND
DIHMLIESANKIS EIGELASSFKRMI 5818 5814 BACKGROUND
PLFTLVKAMEQVC EIGVLY

PLNKVIGGARQVS QFLVLSDNFNQMV 5978 5974 BACKGROUND
PIDNISTLAAHVA DLEKLTTSFKLMV 5979 5975 BACKGROUND
PISFFTNNIQRVA EIGQLTKVFNSMV 5981 5977 BACKGROUND
PLIKLQKLSDLIA EFGNLTHSFFTMS 5982 5978 BACKGROUND
PIMTLTERMQRMT EVGQLMEATNTMA 5983 5979 BACKGROUND
PIQQLSLQSKKVA EVGTLTQNFNLMI 5984 5980 BACKGROUND
RLTRVEQVARRVA ELADLAQSINQMQ 5985 5981 BACKGROUND
PLDMLIGMANAIA ELGRLADAFERMV 5986 5982 BACKGROUND
PLRFLAKEVDVVA EIGQLMTGFNRMK 5987 5983 BACKGROUND
PIDELVGLTNRVA EIGDLTESFHDML 5988 5984 BACKGROUND
PLTRLVAAVQLMR EFSVLADGFNAMA 5989 5985 BACKGROUND
RIQRLAEAATRMA EVGRTVEAFNTML 5990 5986 BACKGROUND
PILDLRRTVQRVA ELGSLAGSVNAMT 5991 5987 BACKGROUND
NLTDLTDKIGLIS EFGMLARDINKMA 5992 5988 BACKGROUND
PLQKTIRSARSVS EIGELVDSFNIMV 5993 5989 BACKGROUND
PLARLAEVSEHAS EIGKAASSFNQMI 5994 5990 BACKGROUND
PLLLTVKEAQRIA ELSLLVEAFNTMR 5995 5991 BACKGROUND
PLHRVQKASADIA ELARLAQSVEQMR 5996 5992 BACKGROUND
PLAKLTHVATRIA EVGELARGFQVMV 5997 5993 BACKGROUND
NIGQVTKLTSNIC ELGHMAQDLNKMS 5998 5994 BACKGROUND
PLLKITTALKNIA EFAEVG

PLRRLESHITTLS EIGLLARAFATMQ 6160 6156 BACKGROUND
PISAIVEATKKVR ELGLLIENFNSMV 6161 6157 BACKGROUND
PLIHMNEVAHNIS EVAELGHALNHMA 6162 6158 BACKGROUND
EVDRMVGAMDRFV EIGRLQGKFNQSV 6163 6159 BACKGROUND
PLNNLIDSMARVE EIGRLIVSFDSMV 6167 6163 BACKGROUND
FIEKITQLVEQIS ELGNLSKAVNKMS 6168 6164 BACKGROUND
PLREAVQGAGRIA ELAALMRALNTMT 6169 6165 BACKGROUND
PVNLAREHCRQIA EIDHLMSSMEQMR 6170 6166 BACKGROUND
AIQKLRETVHKVE ELGELATDLNNMV 6171 6167 BACKGROUND
RLKGILSVTKQAA EVGKLAESVNGMM 6172 6168 BACKGROUND
RIRKLRDEAERAI EIGDLSRSFASIV 6173 6169 BACKGROUND
PVQQLAAVAERVR ELGRLAIAFKSMQ 6175 6171 BACKGROUND
QFKLVRDGAQRFA EVGRLAAMFNTMA 6176 6172 BACKGROUND
PVAKMVGAIKQMA EVGQMAVNLNRLA 6177 6173 BACKGROUND
PLAALTRTMNDIT EIGTLQASFMWMT 6178 6174 BACKGROUND
PLERLIAAMSEIA EIGQALEHLIGCC 6180 6176 BACKGROUND
PVRKLVRQAQFIA ELGQLANEFNQMQ 6181 6177 BACKGROUND
PIDRLVRHIGHVA EIGTVGKVVNDMS 6182 6178 BACKGROUND
PLLASMDFAQHIA ELGELGSSLNNMA 6183 6179 BACKGROUND
PFAWMKAEMDEVA EVGQLMDNFANMA 6184 6180 BACKGROUND
HLRKVESVAIRIA LVSRLG

RVHQVQRNAQRLA EIGQLGTRLVEAG 6348 6348 BACKGROUND
PLLRLERPIRNMA EVAGLVQAVNSML 6349 6349 BACKGROUND
PLARLTLTARQLT DITDLSAAFADMH 6350 6350 BACKGROUND
PLQRLAAQTASIG ELDALIAGLNGML 6351 6351 BACKGROUND
PLRELMHQMRNFA EIGSLAQTFVAMQ 6352 6352 BACKGROUND
RLRCIESAFAAAA ALDALAESTNRSI 6353 6353 BACKGROUND
ALNKLEDYATKMG EYGTLSDALEKMR 6354 6354 BACKGROUND
RFRHLFDAVDRVS ELGLLARHVERMA 6356 6356 BACKGROUND
PIRLLNSRLERIN EIGDLYNHFNNME 6357 6357 BACKGROUND
QFRSLSNLLDAMV ALNELVDSINSLS 6358 6358 BACKGROUND
PLRSLARAVARFG ELRQLTRGFNQMV 6359 6359 BACKGROUND
PLRAVEGVMARIG EFDNLSERLVETG 6360 6360 BACKGROUND
RIGRVQDTVHRMI ELGLLAKDVALLS 6361 6361 BACKGROUND
PVRRIADRIQALG ELVELEQQLDWLT 6362 6362 BACKGROUND
PLRRLERALARVG EVQRLSQRFNAML 6363 6363 BACKGROUND
PLIGIINDVEVLS VYKQVYRTINNLS 6364 6364 BACKGROUND
LFRALAGTTSSYR ELAQLVQAHAELG 6365 6365 BACKGROUND
KLKELSMMIDEVL ELSILQNEIKKMT 6367 6367 BACKGROUND
PMRQLSSLMVRRE ETRLLIVAFNRYI 6368 6368 BACKGROUND
DLLEVRRTAEMFA LFAPLPLAFNSMA 6369 6369 BACKGROUND
PLYRLTQSAALIE ETQDLA

5314

In [24]:
data_df.to_pickle(os.path.join(data_dir, 'af2.p'))

In [44]:
# checked, OK